In [1]:
import openml
from sklearn.model_selection import train_test_split
from test_datasets.dataset_getters import get_pc4_dataset
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import roc_auc_score
from tabpfgen import TabPFGen
from tabpfgen.visuals import visualize_classification_results
from sklearn.datasets import load_breast_cancer
import torch
import pandas as pd
from tabpfn_extensions import unsupervised
from tabpfn import TabPFNClassifier, TabPFNRegressor
from performance_metrics.measure_random_forest_auc import measure_random_forest_auc

In [2]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print("Using device:", device)

Using device: cuda


In [3]:
train, test = get_pc4_dataset()

In [4]:
print(train.columns)

Index(['LOC_BLANK', 'BRANCH_COUNT', 'CALL_PAIRS', 'LOC_CODE_AND_COMMENT',
       'LOC_COMMENTS', 'CONDITION_COUNT', 'CYCLOMATIC_COMPLEXITY',
       'CYCLOMATIC_DENSITY', 'DECISION_COUNT', 'DECISION_DENSITY',
       'DESIGN_COMPLEXITY', 'DESIGN_DENSITY', 'EDGE_COUNT',
       'ESSENTIAL_COMPLEXITY', 'ESSENTIAL_DENSITY', 'LOC_EXECUTABLE',
       'PARAMETER_COUNT', 'HALSTEAD_CONTENT', 'HALSTEAD_DIFFICULTY',
       'HALSTEAD_EFFORT', 'HALSTEAD_ERROR_EST', 'HALSTEAD_LENGTH',
       'HALSTEAD_LEVEL', 'HALSTEAD_PROG_TIME', 'HALSTEAD_VOLUME',
       'MAINTENANCE_SEVERITY', 'MODIFIED_CONDITION_COUNT',
       'MULTIPLE_CONDITION_COUNT', 'NODE_COUNT',
       'NORMALIZED_CYLOMATIC_COMPLEXITY', 'NUM_OPERANDS', 'NUM_OPERATORS',
       'NUM_UNIQUE_OPERANDS', 'NUM_UNIQUE_OPERATORS', 'NUMBER_OF_LINES',
       'PERCENT_COMMENTS', 'LOC_TOTAL', 'c'],
      dtype='object')


# Test quality

In [6]:
from external.tab_pfn_gen.src.tabpfgen import TabPFGen

generator = TabPFGen(n_sgld_steps=200, device=device)

X, y = train.drop("c", axis=1), train["c"].to_list()

X_synth, y_synth = generator.generate_classification(
    X, y,
    n_samples=X.shape[0],
    balance_classes=True,
)


Step 0/200
Step 100/200


In [22]:
clf = RandomForestClassifier().fit(X, y)
print("Train AUC:", roc_auc_score(y, clf.predict_proba(X)[:, 1]))
clf = RandomForestClassifier().fit(X_synth, y_synth)
print("Train AUC:", roc_auc_score(y, clf.predict_proba(X)[:, 1]))

Train AUC: 0.9999201419192179
Train AUC: 0.9566570266554866


/home/mikic202/miniconda3/envs/pt/lib/python3.11/site-packages/sklearn/base.py:486: UserWarning: X has feature names, but RandomForestClassifier was fitted without feature names
  warnings.warn(


# Compare TabPFN

In [7]:
model_unsupervised = unsupervised.TabPFNUnsupervisedModel(
    tabpfn_clf=TabPFNClassifier(),
    tabpfn_reg=TabPFNRegressor()
)

experiment = unsupervised.experiments.GenerateSyntheticDataExperiment(
    task_type='unsupervised'
)

results = experiment.run(
    tabpfn=model_unsupervised,
    X=torch.tensor(train.values.astype('float32')),
    attribute_names=train.columns.tolist(),
    temp=1.0,  # Temperature parameter for sampling
    n_samples=len(train),  # Generate twice as many samples as original data
    indices=range(len(train.columns)),
    device=device,
)

100%|██████████| 38/38 [34:15<00:00, 54.09s/it]


In [29]:
generator = TabPFGen(n_sgld_steps=200, device=device)

X, y = train.drop("c", axis=1), train["c"].to_list()

X_synth, y_synth = generator.generate_classification(
    X, y,
    n_samples=X.shape[0],
    balance_classes=True,
)
X_synth = pd.DataFrame(X_synth, columns=X.columns)


Step 0/200
Step 100/200


In [27]:
x_synth_first_type = experiment.data_synthetic

In [28]:
y_synth_first_type = x_synth_first_type["c"].to_list()
x_synth_first_type= x_synth_first_type.drop(["c", "real_or_synthetic"], axis=1).astype('float32')

In [3]:
from performance_metrics.measure_model_performance import measure_model_performance

In [4]:
generator = TabPFGen(n_sgld_steps=200, device=device)
print(measure_model_performance(generator.generate_classification))

Step 0/200
Step 100/200


/home/mikic202/miniconda3/envs/pt/lib/python3.11/site-packages/sklearn/base.py:486: UserWarning: X has feature names, but RandomForestClassifier was fitted without feature names
  warnings.warn(
/home/mikic202/miniconda3/envs/pt/lib/python3.11/site-packages/sklearn/linear_model/_logistic.py:469: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. OF ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/home/mikic202/miniconda3/envs/pt/lib/python3.11/site-packages/sklearn/base.py:486: UserWarning: X has feature names, but LogisticRegression was fitted without feature names
  warnings.warn(
/home/mikic202/miniconda3/envs/pt/lib/python3.11/site-packages/sklearn/base.py:4

Step 0/200
Step 100/200


/home/mikic202/miniconda3/envs/pt/lib/python3.11/site-packages/sklearn/base.py:486: UserWarning: X has feature names, but RandomForestClassifier was fitted without feature names
  warnings.warn(
/home/mikic202/miniconda3/envs/pt/lib/python3.11/site-packages/sklearn/linear_model/_logistic.py:469: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. OF ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
/home/mikic202/miniconda3/envs/pt/lib/python3.11/site-packages/sklearn/base.py:486: UserWarning: X has feature names, but LogisticRegression was fitted without feature names
  warnings.warn(
/home/mikic202/miniconda3/envs/pt/lib/python3.11/site-packages/sklearn/base.py:4

         dataset  random_forest   xgboost        LR    TabPFN
1  mfeat_zernike       0.971594  0.973724  0.981416  0.983981
0            pc4       0.967096  0.957418  0.850907  0.977617
